In [64]:
import tensorflow as tf
from keras.utils import to_categorical
from keras.models import model_from_json

In [65]:
import keras
from keras.initializers import glorot_uniform
from keras.layers import Activation
from keras import backend as K
from keras.utils.generic_utils import get_custom_objects

In [66]:
from tensorflow import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten, MaxPooling2D, BatchNormalization
from keras.layers.convolutional import Conv2D, Conv1D
from keras.wrappers.scikit_learn import KerasClassifier

In [67]:
from __future__ import division

import sys
import time
import logging

import numpy as np
from scipy.io import loadmat
from os import path
from sklearn import metrics

# change this to the path of mushu if you don't have it in your
# PYTHONPATH already
sys.path.append('../../mushu')
sys.path.append('../')

import libmushu
from libmushu.driver.replayamp import ReplayAmp
from wyrm.types import RingBuffer
import wyrm.processing as proc
from wyrm import io
from wyrm.types import Data, BlockBuffer, RingBuffer

#Classifiers
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
import matplotlib
import matplotlib.pyplot as plt
from sklearn.externals import joblib
from os import listdir
from os.path import isfile, join

In [68]:
logging.basicConfig(format='%(relativeCreated)10.0f %(threadName)-10s %(name)-10s %(levelname)8s %(message)s', level=logging.NOTSET)
logger = logging.getLogger(__name__)

In [69]:
# replay the experiment in real time?
REALTIME = False


TRAIN_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Train.mat'
TEST_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Test.mat'

TRAIN_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Train.mat'
TEST_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Test.mat'

CHANNEL_DATA = '../BCI_Comp_III_Wads_2004/data/eloc64.txt'

TRUE_LABELS = "WQXPLZCOMRKO97YFZDEZ1DPI9NNVGRQDJCUVRMEUOOOJD2UFYPOO6J7LDGYEGOA5VHNEHBTXOO1TDOILUEE5BFAEEXAW_K4R3MRU"

STIMULUS_CODE = {
    # cols from left to right
    1 : "agmsy5",
    2 : "bhntz6",
    3 : "ciou17",
    4 : "djpv28",
    5 : "ekqw39",
    6 : "flrx4_",
    # rows from top to bottom
    7 : "abcdef",
    8 : "ghijkl",
    9 : "mnopqr",
    10: "stuvwx",
    11: "yz1234",
    12: "56789_"
}

MARKER_DEF_TRAIN = {'target': ['target'], 'nontarget': ['nontarget']}
MARKER_DEF_TEST = {i : [i] for i in STIMULUS_CODE.values()}

SEG_IVAL = [0, 800]

In [70]:
def load_bci_TESTdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][60:,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][60:,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][60:,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[60:,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_mat.get('TargetChar')[0][60:]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [71]:
def load_bci_TRAINdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][:60,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][:60,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][:60,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[:60,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_mat.get('TargetChar')[0][:60]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [72]:
## Agregar esto en metrics.py de keras
from keras import backend as K
def precision(y_true, y_pred):
    """Precision metric.

    Only computes a batch-wise average of precision.

    Computes the precision, a metric for multi-label classification of
    how many selected items are relevant.
    """
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
    precision = true_positives / (predicted_positives + K.epsilon())
    return precision

def recall(y_true, y_pred):
    """Recall metric.

    Only computes a batch-wise average of recall.

    Computes the recall, a metric for multi-label classification of
    how many relevant items are selected.
    """
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
    recall = true_positives / (possible_positives + K.epsilon())
    return recall


def f1(y_true, y_pred):
    def recall(y_true, y_pred):
        """Recall metric.

        Only computes a batch-wise average of recall.

        Computes the recall, a metric for multi-label classification of
        how many relevant items are selected.
        """
        true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
        possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
        recall = true_positives / (possible_positives + K.epsilon())
        return recall

    def precision(y_true, y_pred):
        """Precision metric.

        Only computes a batch-wise average of precision.

        Computes the precision, a metric for multi-label classification of
        how many selected items are relevant.
        """
        true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
        predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
        precision = true_positives / (predicted_positives + K.epsilon())
        return precision
    precision = precision(y_true, y_pred)
    recall = recall(y_true, y_pred)
    return 2*((precision*recall)/(precision+recall+K.epsilon()))
    
    def f_05(y_true, y_pred):
        return((1+0.5**2)*(precision*recall)/((0.5**2)*precision+recall+K.epsilon()))


In [73]:


from __future__ import division

import time

import numpy as np

from libmushu.amplifier import Amplifier


class RReeplayAmp(Amplifier):

    def configure(self, data, marker, channels, fs, realtime=True, blocksize_ms=None, blocksize_samples=None):
        """

        Parameters
        ----------
        data
        marker
        channels
        fs
        realtime
        blocksize_ms : float
            blocksize in milliseconds
        blocksize_samples : int
            blocksize in samples

        Raises
        ------
        TypeError :
            if ``blocksize_ms`` and ``blocksize_s`` are given.

        """
        if [blocksize_ms, blocksize_samples].count(None) != 1:
            raise TypeError("blocksize_ms and blocksize_samples are mutually exclusive.")

        self.data = data
        # slow python
        self.marker = marker
        # fast numpy
        self.marker_ts = np.array([ts for ts, s in marker])
        self.marker_s = np.array([s for ts, s in marker])
        self.channels = channels
        self.fs = fs
        self.realtime = realtime

        if blocksize_ms:
            samples = fs * (blocksize_ms / 1000)
            if not samples.is_integer():
                raise ValueError("Resulting blocksize is not integer, please fix the blocksize_ms.")
            self.samples = samples
        if blocksize_samples:
            self.samples = blocksize_samples

    def start(self):
        self.last_sample_time = time.time()
        self.pos = 0

    def stop(self):
        pass

    def get_data(self):
        """

        Returns
        -------
        chunk, markers: Markers is time in ms since relative to the
        first sample of that block.

        """
        if self.realtime:
            elapsed = time.time() - self.last_sample_time
            blocks = (self.fs * elapsed) // self.samples
            samples = int(blocks * self.samples)
            
        else:
            samples = self.samples
      
        elapsed = samples / self.fs
        self.last_sample_time += elapsed
        # data
        chunk = self.data[self.pos:int(self.pos+samples)]
        #self.data = self.data[samples:]
        # markers

        # slow python version
        #markers = [x for x in self.marker if x[0] < elapsed * 1000]
        #self.marker = [x for x in self.marker if x[0] >= elapsed * 1000]
        #self.marker = [[x[0] - elapsed * 1000, x[1]] for x in self.marker]

        # fast numpy version
        mask = self.marker_ts < (elapsed * 1000) 
        markers = list(zip(self.marker_ts[mask], self.marker_s[mask]))
        self.marker_ts = self.marker_ts[~mask]
        self.marker_s = self.marker_s[~mask]
        self.marker_ts -= elapsed * 1000

        self.pos += samples
        return chunk, markers

    def get_channels(self):
        return self.channels

    def get_sampling_frequency(self):
        return self.fs

    @staticmethod
    def is_available():
        return True


In [74]:
def online_experiment(amp, cfy, subject):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    
    file = open('sim_training_CCNN'+subject+'.txt', 'w')
    file.write('CCNN Online simulation')
    file.write('CCNN Online simulation'+subject)
    
    # csv results file
    filename = 'results/'+subject+'/Results_CCNN_'+subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,\
    precision_acum,f1_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames) 
    
    chfilename = 'results/'+subject+'/CharacterResults_CCNN_'+subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames) 



    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [20 / fn], btype='low')
    b_high, a_high = proc.signal.butter(5, [.1 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
    zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
  
        # band-pass and subsample
        cnt = proc.subsample(cnt, 120)
      
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
        cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, [0, 650], newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, [0, 650], newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = create_fv(epo)
        fv_train = create_fv(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        X = fv.data
        X = X.reshape(X.shape[0],X.shape[1], X.shape[2], 1)
        
        cfy_out = cfy.predict(X)[:,1]
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict_classes(X) 
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, cfy_out)
        
        report = metrics.classification_report(y_true, y_pred)
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
          
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, n_trial))
                    correct_letter = True
                    
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                            current_letter, int(markers_processed/12)))

                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(f1)+','+str(accuracy))


                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)

                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))


            markers_processed += 1

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()

    amp.stop()


In [75]:
class CustomSigmoid(Activation):
    
    def __init__(self, activation, **kwargs):
        super(CustomSigmoid, self).__init__(activation, **kwargs)
        self.__name__ = 'customSigmoid'


def customSigmoid(x):
    return (K.tanh(2/3*x) * 1.7159)

get_custom_objects().update({'customSigmoid': CustomSigmoid(customSigmoid)})
#get_custom_objects().update({'custom_sigmoid': Activation(custom_sigmoid)})

In [76]:
def train(filename):
    cnt = load_bci_TRAINdata(filename)


    fv = preprocessing_CCNNbis(cnt, MARKER_DEF_TRAIN)
    
#     X = fv.data
#     y = fv.axes[0]
    clf = train_CNN(fv)

    return clf

In [77]:
def create_fv(epo):
    mean = np.mean(epo.data, axis=1)
    mean_ = []
    mean_.extend(78*[mean])
    mean_ = np.array(mean_)
    mean_ = np.swapaxes(mean_, 0, 1)

    std = np.std(epo.data, axis=1)
    std_ = []
    std_.extend(78*[std])
    std_ = np.array(std_)
    std_ = np.swapaxes(std_, 0, 1)

    Iij = (epo.data - mean_)/std_
    fv = epo.copy(data=Iij, fs=120)
    return fv
        

# 1. Preprocessing

In [78]:
def preprocessing_CCNNbis(dat, MRK_DEF, *args, **kwargs):
    dat = proc.subsample(dat, 120)
    
    fs_n = dat.fs / 2
    b, a = proc.signal.butter(5, [20 / fs_n], btype='low')
    dat = proc.lfilter(dat, b, a)
    b, a = proc.signal.butter(5, [0.1 / fs_n], btype='high')
    dat = proc.lfilter(dat, b, a)
   
    epo = proc.segment_dat(dat, MRK_DEF, [0, 650])
    
    mean = np.mean(epo.data, axis=1)
    mean_ = []
    mean_.extend(78*[mean])
    mean_ = np.array(mean_)
    mean_ = np.swapaxes(mean_, 0, 1)

    std = np.std(epo.data, axis=1)
    std_ = []
    std_.extend(78*[std])
    std_ = np.array(std_)
    std_ = np.swapaxes(std_, 0, 1)

    Iij = (epo.data - mean_)/std_
    fv = epo.copy(data=Iij, fs=120)

    return fv

In [79]:
subject = 'A'
if subject == 'A':
    TRAIN_DATA = TRAIN_DATA_A
elif subject == 'B':
    TRAIN_DATA = TRAIN_DATA_B
data_m = loadmat(TRAIN_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars

# 2. Model Construction

In [80]:
class CCNN:
    @staticmethod
    def build(height, width, depth):
        model = Sequential()
        inputShape = (height, width, depth)
        
        # Layer 1: CONV => Custom_Sigmoid
        model.add(Conv2D(10, (1,64), input_shape=inputShape, name='L1'))
        model.add(Activation('customSigmoid'))
        
        # Layer 2: CONV => Custom_Sigmoid
        model.add(Conv2D(50, (13,1), name='L2'))
        model.add(Activation('customSigmoid'))
        
        # Layer 3: FC => Sigmoid
        model.add(Flatten())
        model.add(Dense(100, activation = 'sigmoid', name='L3'))
        
        # Output layer: softmax classifier
        model.add(Dense(2, activation = 'softmax', name='OutputLayer'))
        
        # return the constructed network architecture
        return model

In [81]:
def train_CNN(fv):
    X = fv.data
    X_train = X.reshape(X.shape[0],X.shape[1], X.shape[2], 1)
    y_train = fv.axes[0]

    #Creating the architecture (layers)
    n_features = X_train.shape[1]
    
    model = CCNN.build(width=64, height=78, depth=1)
    model.compile(optimizer='sgd',
              loss='binary_crossentropy',       
              metrics=['accuracy', precision, recall, f1], 
              weighted_metrics = [f1]) 
    
    n_P300 = X_train[y_train == 1].shape[0]
    n_nonP300 = X_train[y_train == 0].shape[0]
    H = model.fit(X_train, to_categorical(y_train), epochs = 100, validation_split = 0.2, 
               class_weight = {1: n_nonP300/n_P300*0.4, 0: n_P300/n_nonP300})

    return model

In [34]:
clf = train(TRAIN_DATA)

Train on 8640 samples, validate on 2160 samples
Epoch 1/100
8640/8640 [==============================] - 7s 819us/step - loss: 0.3195 - acc: 0.1885 - precision: 0.1885 - recall: 0.1885 - f1: 0.1885 - weighted_f1: 0.1019 - val_loss: 0.3138 - val_acc: 0.1667 - val_precision: 0.1667 - val_recall: 0.1667 - val_f1: 0.1667 - val_weighted_f1: 0.0843
Epoch 2/100
8640/8640 [==============================] - 6s 740us/step - loss: 0.3055 - acc: 0.1789 - precision: 0.1789 - recall: 0.1789 - f1: 0.1789 - weighted_f1: 0.0970 - val_loss: 0.3051 - val_acc: 0.1806 - val_precision: 0.1806 - val_recall: 0.1806 - val_f1: 0.1806 - val_weighted_f1: 0.0913
Epoch 3/100
8640/8640 [==============================] - 6s 691us/step - loss: 0.2901 - acc: 0.2620 - precision: 0.2620 - recall: 0.2620 - f1: 0.2620 - weighted_f1: 0.1373 - val_loss: 0.2928 - val_acc: 0.3190 - val_precision: 0.3190 - val_recall: 0.3190 - val_f1: 0.3190 - val_weighted_f1: 0.1601
Epoch 4/100
8640/8640 [==============================] - 6s 6

8640/8640 [==============================] - 5s 590us/step - loss: 0.1816 - acc: 0.7388 - precision: 0.7388 - recall: 0.7388 - f1: 0.7388 - weighted_f1: 0.3712 - val_loss: 0.2778 - val_acc: 0.7014 - val_precision: 0.7014 - val_recall: 0.7014 - val_f1: 0.7014 - val_weighted_f1: 0.3506
Epoch 56/100
8640/8640 [==============================] - 6s 647us/step - loss: 0.1822 - acc: 0.7410 - precision: 0.7410 - recall: 0.7410 - f1: 0.7410 - weighted_f1: 0.3724 - val_loss: 0.2695 - val_acc: 0.6949 - val_precision: 0.6949 - val_recall: 0.6949 - val_f1: 0.6949 - val_weighted_f1: 0.3476
Epoch 57/100
8640/8640 [==============================] - 6s 669us/step - loss: 0.1811 - acc: 0.7380 - precision: 0.7380 - recall: 0.7380 - f1: 0.7380 - weighted_f1: 0.3698 - val_loss: 0.2719 - val_acc: 0.7083 - val_precision: 0.7083 - val_recall: 0.7083 - val_f1: 0.7083 - val_weighted_f1: 0.3541
Epoch 58/100
8640/8640 [==============================] - 5s 627us/step - loss: 0.1806 - acc: 0.7427 - precision: 0.742

In [96]:
filename = 'Trained Classifiers/'+subject+'/CCNN_'+subject+'.json'
weights_filename = 'Trained Classifiers/'+subject+'/CCNN_weights_'+subject+'.h5'

In [35]:
# serialize model to JSON
model_json = clf.to_json()
with open(filename, "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
clf.save_weights(weights_filename)
print("Saved model to disk")


Saved model to disk


In [97]:
# load json and create model
json_file = open(filename, 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights(weights_filename)
print("Loaded model from disk")
# evaluate loaded model on test data
loaded_model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 
clf = loaded_model

Loaded model from disk


# 2. Simulation

In [98]:
bbuffer = BlockBuffer(2)
cnt = load_bci_TESTdata(TRAIN_DATA)

In [99]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=2)

In [100]:

online_experiment(amp, clf, subject)


DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 310.4407787322998
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 15.956640243530273
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 18.952131271362305


C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true samples.
  'recall', 'true', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 
DEBUG:__main__:5


Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.75
time 22.937536239624023
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.3333333333333333 	f1:  0.5 	accuracy:  0.6
time 16.95537567138672


DEBUG:__main__:Markers processed: 
DEBUG:__main__:6


...

Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.6390041493775933 	precision:  0.26985981308411217 	f1:  0.37946611909650924 	accuracy:  0.6518433179723502
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 21.9419002532959
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.638121546961326 	precision:  0.26985981308411217 	f1:  0.3793103448275862 	accuracy:  0.6516931582584657
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 22.9034423828125


DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_ektlbwxepouil1eroouzh
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_ektlbwxepouil1eroouzh


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.638121546961326 	precision:  0.26970227670753066 	f1:  0.37915469839967175 	accuracy:  0.6515430677107323
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 22.9034423828125
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.638121546961326 	precision:  0.26970227670753066 	f1:  0.37915469839967175 	accuracy:  0.6516233018650702
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 21.939754486083984


DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_ektlbwxepouil1eroouzhq


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.638121546961326 	precision:  0.26954492415402564 	f1:  0.37899917965545526 	accuracy:  0.6514732965009208
Character prediction metrics...
Current accuracy: 79.16666666666666
24/25 characters predicted
Accuracy: 79.16666666666666


# INTERSUJETO

In [43]:
def online_experiment_intersujeto(amp, cfy, inter_subject):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    
    file = open('sim_training_CCNN'+inter_subject+'.txt', 'w')
    file.write('CCNN Online simulation '+inter_subject)
    
    # csv results file
    filename = 'results/Intersujeto/'+inter_subject+'/Results_CCNN_'+inter_subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)

    chfilename = 'results/Intersujeto/'+inter_subject+'/CharacterResults_CCNN_'+inter_subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames) 
    

    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [20 / fn], btype='low')
    b_high, a_high = proc.signal.butter(5, [.1 / fn], btype='high')
    
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
    zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # band-pass and subsample
        cnt = proc.subsample(cnt, 120)
      
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
        cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, [0, 650], newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, [0, 650], newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = create_fv(epo)
        fv_train = create_fv(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        X = fv.data
        X = X.reshape(X.shape[0],X.shape[1], X.shape[2], 1)
        
        cfy_out = cfy.predict(X)[:,1]
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict_classes(X) 
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, cfy_out)
        
        report = metrics.classification_report(y_true, y_pred)
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
               
              
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, n_trial))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                           current_letter, int(markers_processed/12)))

                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))
        

            markers_processed += 1

                
#             if (markers_processed%12 == 0) & (markers_processed != 180) & (not correct_letter):
#                 current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
#                 if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                     file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                   current_letter, int(markers_processed/12)))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
#                     correct_letter = True
           
#             elif markers_processed == 180: # 12 trials x 15 repetitions = 180
#                 endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
#                 # Set all probabilities to zero
#                 letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
#                 markers_processed = 0
#                 if not correct_letter:
#                     file.write('\n\nFailed to predict character #{} in 15 trials'.format(len(endresult)))
#                     file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
                    
#                 correct_letter = False
# #                 current_letter_idx += 1
# #                 print('letter idx', current_letter_idx)
# #                 current_letter = TRUE_LABELS[current_letter_idx].lower()
#             markers_processed += 1
#         print(letter_prob)
#         logger.debug("".join([i[0] for i in sorted(letter_prob.items(), key=lambda x: x[1], reverse=True)]).replace(current_letter, " %s " % current_letter))

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()
    resultsFile.close()

    amp.stop()


In [50]:
inter_subject = 'B-clfA'
if inter_subject == 'A-clfB':
    TEST_DATA = TRAIN_DATA_A
    subject = 'B'
elif inter_subject == 'B-clfA':
    TEST_DATA = TRAIN_DATA_B  
    subject = 'A'
data_m = loadmat(TEST_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars
TRUE_LABELS

'KOJDWZEUEWWFOEBHXTQTTZUMO'

## 1. Training (off-line)

In [51]:
filename = 'Trained Classifiers/'+subject+'/CCNN_'+subject+'.json'
weights_filename = 'Trained Classifiers/'+subject+'/CCNN_weights_'+subject+'.h5'

In [52]:
# load json and create model
json_file = open(filename, 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights(weights_filename)
print("Loaded model from disk")
# evaluate loaded model on test data
loaded_model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 
clf = loaded_model

Loaded model from disk


## 2. Online experiment

In [53]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TEST_DATA)

In [54]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [55]:
online_experiment_intersujeto(amp, clf, inter_subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 
DEBUG:__main__:5
DEBUG:__main__:Markers processed: 
DEBUG:__main__:6
DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8


Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  1.0 	f1:  1.0 	accuracy:  1.0
time 141.12353324890137
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  1.0 	f1:  1.0 	accuracy:  1.0
time 11.967182159423828
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.6666666666666666
time 10.970592498779297
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.3333333333333333 	f1:  0.5 	accuracy:  0.5
time 12.964010238647461
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.25 	f1:  0.4 	accuracy:  0.4
time 13.961315155029297
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.2 	f1:  0.33333333333333337 	accuracy:  0.3333333333333333
time 14.963150024414062
Predicho:  

DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16



P300 classification metrics...
recall:  1.0 	precision:  0.2 	f1:  0.33333333333333337 	accuracy:  0.5555555555555556
time 12.964487075805664
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.3333333333333333 	f1:  0.5 	accuracy:  0.6
time 11.965751647949219
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.3333333333333333 	f1:  0.5 	accuracy:  0.6363636363636364
time 9.974002838134766
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.3333333333333333 	f1:  0.5 	accuracy:  0.6666666666666666
time 11.981725692749023
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.42857142857142855 	f1:  0.6 	accuracy:  0.6923076923076923
time 11.967182159423828
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.42857142857142855 	f1:  0.6 	accuracy:  0.71

DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 
DEBUG:__main__:19
DEBUG:__main__:Markers processed: 
DEBUG:__main__:20
DEBUG:__main__:Markers processed: 
DEBUG:__main__:21
DEBUG:__main__:Markers processed: 
DEBUG:__main__:22
DEBUG:__main__:Markers processed: 


...

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5352697095435685 	precision:  0.24293785310734464 	f1:  0.3341968911917099 	accuracy:  0.6445366528354081
Character prediction metrics...
Current accuracy: 26.08695652173913
23/25 characters predicted
time 44.21401023864746
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5352697095435685 	precision:  0.24293785310734464 	f1:  0.3341968911917099 	accuracy:  0.6446185757086886
Character prediction metrics...
Current accuracy: 26.08695652173913
23/25 characters predicted
time 40.92049598693848
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5352697095435685 	precision:  0.24278544542032623 	f1:  0.3340526542943461 	accuracy:  0.6444700460829493
Character prediction metrics...
Current accuracy: 26.08695652173913
23/25 characters predicted
time 28.935909271240234


DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:doje9dfue3sfmbgbinptgyg
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:doje9dfue3sfmbgbinptgyg
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:doje9dfue3sfmbgbinptgyg


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5352697095435685 	precision:  0.24278544542032623 	f1:  0.3340526542943461 	accuracy:  0.644551946556093
Character prediction metrics...
Current accuracy: 26.08695652173913
23/25 characters predicted
time 38.93613815307617
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5352697095435685 	precision:  0.2426332288401254 	f1:  0.3339085418464193 	accuracy:  0.6444035006909259
Character prediction metrics...
Current accuracy: 26.08695652173913
23/25 characters predicted
time 36.901235580444336
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.5345303867403315 	precision:  0.2426332288401254 	f1:  0.33376455368693403 	accuracy:  0.6442551231867373
Character prediction metrics...

DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:doje9dfue3sfmbgbinptgygm



Current accuracy: 26.08695652173913
23/25 characters predicted
time 48.380136489868164
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5345303867403315 	precision:  0.2426332288401254 	f1:  0.33376455368693403 	accuracy:  0.6443370165745856
Character prediction metrics...
Current accuracy: 29.166666666666668
24/25 characters predicted
Accuracy: 29.166666666666668


## Sujeto C

In [82]:
def load_bci_TRAINdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[:30,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [83]:
def load_bci_TESTdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[30:,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [84]:
labels = 'CATDOGFISHWATERBOWLHATHATGLOVESHOESFISHRAT'
path_ = '../BCI_Comp_II_2003/data/'
datafiles = [join(path_,f) for f in listdir(path_) if isfile(join(path_, f))]
training_set = [f for i,f in enumerate(datafiles) if '12' not in f and 'eloc64' not in f]
testing_set = [f for i,f in enumerate(datafiles) if '12' in f and 'eloc64' not in f]

In [85]:
# load the training set
dat_train = load_bci_TRAINdata2(training_set)


In [86]:
TRUE_LABELS = labels[30:]
TRUE_LABELS

'SHOESFISHRAT'

### Training

In [87]:
def train_d2(dat):
    cnt = dat
    fv = preprocessing_CCNNbis(cnt, MARKER_DEF_TRAIN)
    clf = train_CNN(fv)
    return clf

In [88]:
clf = train_d2(dat_train)

Train on 4349 samples, validate on 1088 samples
Epoch 1/100
4349/4349 [==============================] - 4s 817us/step - loss: 0.2861 - acc: 0.2566 - precision: 0.2566 - recall: 0.2566 - f1: 0.2566 - weighted_f1: 0.1365 - val_loss: 0.2745 - val_acc: 0.4035 - val_precision: 0.4035 - val_recall: 0.4035 - val_f1: 0.4035 - val_weighted_f1: 0.2027
Epoch 2/100
4349/4349 [==============================] - 3s 660us/step - loss: 0.2504 - acc: 0.5029 - precision: 0.5029 - recall: 0.5029 - f1: 0.5029 - weighted_f1: 0.2549 - val_loss: 0.2549 - val_acc: 0.5248 - val_precision: 0.5248 - val_recall: 0.5248 - val_f1: 0.5248 - val_weighted_f1: 0.2637
Epoch 3/100
4349/4349 [==============================] - 3s 619us/step - loss: 0.2300 - acc: 0.5859 - precision: 0.5859 - recall: 0.5859 - f1: 0.5859 - weighted_f1: 0.2971 - val_loss: 0.2449 - val_acc: 0.6176 - val_precision: 0.6176 - val_recall: 0.6176 - val_f1: 0.6176 - val_weighted_f1: 0.3103
Epoch 4/100
4349/4349 [==============================] - 3s 6

4349/4349 [==============================] - 3s 640us/step - loss: 0.1126 - acc: 0.8487 - precision: 0.8487 - recall: 0.8487 - f1: 0.8487 - weighted_f1: 0.4260 - val_loss: 0.2312 - val_acc: 0.8097 - val_precision: 0.8097 - val_recall: 0.8097 - val_f1: 0.8097 - val_weighted_f1: 0.4054
Epoch 29/100
4349/4349 [==============================] - 3s 710us/step - loss: 0.1104 - acc: 0.8499 - precision: 0.8499 - recall: 0.8499 - f1: 0.8499 - weighted_f1: 0.4260 - val_loss: 0.2387 - val_acc: 0.7978 - val_precision: 0.7978 - val_recall: 0.7978 - val_f1: 0.7978 - val_weighted_f1: 0.3990
Epoch 30/100
4349/4349 [==============================] - 3s 735us/step - loss: 0.1115 - acc: 0.8563 - precision: 0.8563 - recall: 0.8563 - f1: 0.8563 - weighted_f1: 0.4294 - val_loss: 0.2295 - val_acc: 0.8042 - val_precision: 0.8042 - val_recall: 0.8042 - val_f1: 0.8042 - val_weighted_f1: 0.4024
Epoch 31/100
4349/4349 [==============================] - 3s 708us/step - loss: 0.1094 - acc: 0.8542 - precision: 0.854

4349/4349 [==============================] - 3s 632us/step - loss: 0.0883 - acc: 0.8864 - precision: 0.8864 - recall: 0.8864 - f1: 0.8864 - weighted_f1: 0.4438 - val_loss: 0.2681 - val_acc: 0.8061 - val_precision: 0.8061 - val_recall: 0.8061 - val_f1: 0.8061 - val_weighted_f1: 0.4030
Epoch 56/100
4349/4349 [==============================] - 3s 588us/step - loss: 0.0862 - acc: 0.8848 - precision: 0.8848 - recall: 0.8848 - f1: 0.8848 - weighted_f1: 0.4425 - val_loss: 0.2641 - val_acc: 0.8217 - val_precision: 0.8217 - val_recall: 0.8217 - val_f1: 0.8217 - val_weighted_f1: 0.4113
Epoch 57/100
4349/4349 [==============================] - 3s 627us/step - loss: 0.0855 - acc: 0.8901 - precision: 0.8901 - recall: 0.8901 - f1: 0.8901 - weighted_f1: 0.4454 - val_loss: 0.2651 - val_acc: 0.8153 - val_precision: 0.8153 - val_recall: 0.8153 - val_f1: 0.8153 - val_weighted_f1: 0.4074
Epoch 58/100
4349/4349 [==============================] - 3s 691us/step - loss: 0.0848 - acc: 0.8901 - precision: 0.890

4349/4349 [==============================] - 3s 644us/step - loss: 0.0756 - acc: 0.9023 - precision: 0.9023 - recall: 0.9023 - f1: 0.9023 - weighted_f1: 0.4523 - val_loss: 0.3068 - val_acc: 0.8097 - val_precision: 0.8097 - val_recall: 0.8097 - val_f1: 0.8097 - val_weighted_f1: 0.4050
Epoch 83/100
4349/4349 [==============================] - 3s 620us/step - loss: 0.0719 - acc: 0.9062 - precision: 0.9062 - recall: 0.9062 - f1: 0.9062 - weighted_f1: 0.4540 - val_loss: 0.3104 - val_acc: 0.8208 - val_precision: 0.8208 - val_recall: 0.8208 - val_f1: 0.8208 - val_weighted_f1: 0.4104
Epoch 84/100
4349/4349 [==============================] - 3s 620us/step - loss: 0.0733 - acc: 0.9066 - precision: 0.9066 - recall: 0.9066 - f1: 0.9066 - weighted_f1: 0.4543 - val_loss: 0.3091 - val_acc: 0.8199 - val_precision: 0.8199 - val_recall: 0.8199 - val_f1: 0.8199 - val_weighted_f1: 0.4103
Epoch 85/100
4349/4349 [==============================] - 3s 611us/step - loss: 0.0721 - acc: 0.9101 - precision: 0.910

In [89]:
subject = 'C'
filename = 'Trained Classifiers/'+subject+'/CCNN_'+subject+'.json'
weights_filename = 'Trained Classifiers/'+subject+'/CCNN_weights_'+subject+'.h5'

In [90]:
# serialize model to JSON
model_json = clf.to_json()
with open(filename, "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
clf.save_weights(weights_filename)
print("Saved model to disk")


Saved model to disk


In [24]:
# load json and create model
json_file = open(filename, 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights(weights_filename)
print("Loaded model from disk")
# evaluate loaded model on test data
loaded_model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 
clf = loaded_model

Loaded model from disk


### Online experiment

In [91]:
bbuffer = BlockBuffer(12)
dat_test = load_bci_TESTdata2(training_set)
cnt = dat_test

In [92]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [93]:
online_experiment(amp, clf, subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 143.1255340576172
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 15.95759391784668
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 17.955780029296875
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.75
time 16.95561408996582
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8
time 13.9617919921875
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8333333333333334
time 14.958858489990234
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification m

DEBUG:__main__:Markers processed: 
DEBUG:__main__:8
DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.7777777777777778
time 12.965202331542969
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8
time 16.95537567138672
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  1.0 	f1:  0.5 	accuracy:  0.8181818181818182
time 14.960050582885742
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.5 	precision:  1.0 	f1:  0.6666666666666666 	accuracy:  0.8333333333333334
time 23.93484115600586
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  1.0 	f1:  0.6666666666666666 	accuracy:  0.8461538461538461
time 17.951488494873047
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  1.0 	f1:  0.6666666666666666 	accuracy:

DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 
DEBUG:__main__:19


...

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5120481927710844 	precision:  0.37037037037037035 	f1:  0.42983565107458915 	accuracy:  0.7723372034326098
Character prediction metrics...
Current accuracy: 20.0
10/12 characters predicted
time 23.935317993164062
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.37037037037037035 	f1:  0.4292929292929293 	accuracy:  0.7719475277497477
Character prediction metrics...
Current accuracy: 20.0
10/12 characters predicted
time 19.94776725769043
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.37037037037037035 	f1:  0.4292929292929293 	accuracy:  0.7720625315179022
Character prediction metrics...
Current accuracy: 20.0
10/12 characters predicted
time 18.950223922729492
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.

DEBUG:__main__:Markers processed: 
DEBUG:__main__:175
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:yhcmbfngmf
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:yhcmbfngmf
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:yhcmbfngmf
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:yhcmbfngmf
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:yhcmbfngmf
DEBUG:__main__:Markers processed: 


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.3695652173913043 	f1:  0.4287515762925599 	accuracy:  0.7719033232628398
Character prediction metrics...
Current accuracy: 20.0
10/12 characters predicted
time 19.946575164794922
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.3695652173913043 	f1:  0.4287515762925599 	accuracy:  0.7720181177654756
Character prediction metrics...
Current accuracy: 20.0
10/12 characters predicted
time 16.95537567138672
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.368763557483731 	f1:  0.42821158690176325 	accuracy:  0.7716297786720322
Character prediction metrics...
Current accuracy: 20.0
10/12 characters predicted
time 17.95196533203125
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.36876

DEBUG:__main__:180
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:yhcmbfngmfa


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5105105105105106 	precision:  0.36796536796536794 	f1:  0.42767295597484273 	accuracy:  0.7714716223003516
Character prediction metrics...
Current accuracy: 27.27272727272727
11/12 characters predicted
Accuracy: 27.27272727272727
